In [2]:
import numpy as np
import matplotlib.pyplot as plt

import matplotlib.style
import matplotlib as mpl
mpl.style.use('classic')

import baraffe_tables
from baraffe_tables.table_search import baraffe_table_search

from astropy.table import Table
from astropy import units as u
from astropy.constants import G

import mesa_helper as mh
import os
import shutil

%matplotlib inline

In [3]:
mJtomSun = u.jupiterMass.to(u.solMass)
mJtoGrams = u.jupiterMass.to(u.g)

rJtorSun = u.jupiterRad.to(u.solRad)
rJtoCm = u.jupiterRad.to(u.cm)

print(mJtomSun)
print(mJtoGrams)
print(rJtorSun)
print(rJtoCm)


0.0009545942339693249
1.8981245973360504e+30
0.10276268506540176
7149200000.0


In [4]:
print(5*rJtoCm)

35746000000.0


In [6]:
#jupiter masses. note that the last 2 in this list (0.25, 0.2 Mj) weren't created successfully, so don't try to relax them
Minit = np.round(np.logspace(np.log10(0.2),np.log10(20.), num=20),2)[::-1]

Minit = Minit[::4]
print(Minit)

#jupiter radii
#Rinit = np.array((10.0,7.5,5.0,3.0,2.5,2.0,1.75,1.5,1.25,1.0))

Rinit = np.array((5.0,2.0,1.0))

#overall metallicities
Zinit = np.array((0.01,0.025,0.05,0.1))

#specific entropies
#Sinit = np.array((8.0,9.0,10.0,11.0))

Sinit = np.array((8.0,11.0))

# composition profiles
#comps = ['uniform','linear','exponential','gaussian','core_uniform','core_linear','core_exponential','core_gaussian']
comps = ['linear','uniform']

# mixing length alphas
alphas = np.array((1.0,1.5,2.0))

[20.    7.59  2.88  1.09  0.41]


In [7]:
pwd

'/Users/emily/Documents/astro/giant_planets/science_runs'

In [8]:
ls ../1_created_models/*_2.0*.mod | wc -l

zsh:1: no matches found: ../1_created_models/*_2.0*.mod
       0


# All models except the inert core model (see below)

In [10]:
os.chdir('/Users/emily/Documents/astro/giant_planets/science_runs/3_evolved_models')

create_models_dir = '/Users/emily/Documents/astro/giant_planets/science_runs/1_created_models'
relax_models_dir = '/Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models'
evolve_models_dir = '/Users/emily/Documents/astro/giant_planets/science_runs/3_evolved_models'

for i, m in enumerate(Minit):
    for j, r in enumerate(Rinit):
        for k, z in enumerate(Zinit):
            for l, comp in enumerate(comps):
                for n, s in enumerate(Sinit):
                    for a, alpha in enumerate(alphas):

                        this_comp_dir_relax = "{0}_relaxed".format(comp)
                        this_comp_dir_evolve = "{0}_evolved".format(comp)
                        
                        inlist_evolve = mh.Inlist('./inlist_evolve')
                        relax_model_filename = "{0}/{1}/planet_relax_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}.mod".format(relax_models_dir, this_comp_dir_relax, m, r, z, comp, s)
                        #relax_profile_filename = "{0}/{1}/planet_relax_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}.profile".format(relax_models_dir, this_comp_dir_relax, m, r, z, comp, s)
                        #relax_composition_filename = "{0}/{1}/composition_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}.dat".format(relax_models_dir, this_comp_dir_relax, m, r, z, comp, s)
                        #relax_entropy_filename = "{0}/{1}/entropy_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}.dat".format(relax_models_dir, this_comp_dir_relax, m, r, z, comp, s)
    
                        evolve_model_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}.mod".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        evolve_profile_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}.profile".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        history_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}.history".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        profile_folder_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}_profiles/".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        # only proceed if (1) the 'relaxed' model for the above parameter combination exists and 
                        #                 (2) the 'evolved' model does not *yet* exist
                        if os.path.isfile(relax_model_filename) and not os.path.isfile(evolve_model_filename):
                            print("Minit is {0}, Rinit is {1}, Zinit is {2}, comp is {3}, Sinit is {4}".format(m,r,z,comp,s))
                            
                            inlist_evolve.set_option('load_model_filename', relax_model_filename)
                            inlist_evolve.set_option('save_model_filename', evolve_model_filename)
                            inlist_evolve.set_option('filename_for_profile_when_terminate', evolve_profile_filename)
                            inlist_evolve.set_option('mixing_length_alpha', alpha)
        
                            # edit rn script
                            f = open('./rn_template'.format(m), 'r')
                            g = f.read()
                            f.close()
                            #print(g)
                            #g = g.replace("<<relax_profile_name>>", relax_profile_filename)
                            g = g.replace("<<evolve_model_filename>>", evolve_model_filename)
                            
                            h = open('./rn_temp'.format(m), 'w')
                            h.write(g)
                            h.close()
                            shutil.copyfile('./rn_temp'.format(m),'./rn'.format(m))
                            
                            # execute mk, rn scripts
                            os.system('./mk')
                            os.system('./rn')
                            os.system('mv ./LOGS/history.data {0}'.format(history_filename))
                            os.system('mkdir {0}'.format(profile_folder_filename))
                            os.system('mv ./LOGS/profile*.data {0}'.format(profile_folder_filename))
                            os.system('rm ./LOGS/*')
                            
                            print("")
                            print("")
                            
                        else:
                            continue
                            

Minit is 20.0, Rinit is 5.0, Zinit is 0.01, comp is linear, Sinit is 11.0
Set load_model_filename to '/Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models/linear_relaxed/planet_relax_20.0_Mj_5.0_Rj_zbar=0.01_linear_s=11.0.mod'
Set save_model_filename to '/Users/emily/Documents/astro/giant_planets/science_runs/3_evolved_models/linear_evolved/planet_evolve_20.0_Mj_5.0_Rj_zbar=0.01_linear_s=11.0_alpha=1.0.mod'
Set filename_for_profile_when_terminate to '/Users/emily/Documents/astro/giant_planets/science_runs/3_evolved_models/linear_evolved/planet_evolve_20.0_Mj_5.0_Rj_zbar=0.01_linear_s=11.0_alpha=1.0.profile'
Set mixing_length_alpha to 1d0
gfortran -fopenmp -o ../star  run_star_extras.o run_star.o  run.o  -L/Users/emily/mesa-24.08.1/lib -lstar -lgyre_mesa -lgyre -lionization -latm -lcolors -lturb -lstar_data -lnet -leos -lkap -lrates -lneu -lchem -linterp_2d -linterp_1d -lnum -lauto_diff -lforum -lmtx -lconst -lmath -lutils `mesasdk_crmath_link` `mesasdk_lapack95_link

ld: warning: ignoring duplicate libraries: '-lblas', '-llapack', '-lz'


 reading user weak rate file /Users/emily/mesa-24.08.1/data/rates_data/rate_tables/S13_r_be7_wk_li7.h5
 version_number r24.08.1
 read inlist_evolve
 extras_controls: eos initialized
load saved model /Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models/linear_relaxed/planet_relax_20.0_Mj_5.0_Rj_zbar=0.01_linear_s=11.0.mod

 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z00x.bin                                                                                                                                                                                     
 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z60x.bin                                                                                                                                                                                     
 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-2

ld: warning: ignoring duplicate libraries: '-lblas', '-llapack', '-lz'


run inlist_evolve_header
DATE: 2025-08-06
TIME: 15:19:36
 reading user weak rate file /Users/emily/mesa-24.08.1/data/rates_data/rate_tables/S13_r_be7_wk_li7.h5
 version_number r24.08.1
 read inlist_evolve
 extras_controls: eos initialized
load saved model /Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models/linear_relaxed/planet_relax_20.0_Mj_5.0_Rj_zbar=0.01_linear_s=11.0.mod

 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z00x.bin                                                                                                                                                                                     
 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z60x.bin                                                                                                                                                                                     
 Lo

...

run inlist_evolve_header
DATE: 2025-08-07
TIME: 02:36:50
 reading user weak rate file /Users/emily/mesa-24.08.1/data/rates_data/rate_tables/S13_r_be7_wk_li7.h5
 version_number r24.08.1
 read inlist_evolve
 extras_controls: eos initialized
load saved model /Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models/uniform_relaxed/planet_relax_0.41_Mj_2.0_Rj_zbar=0.1_uniform_s=11.0.mod

 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z00x.bin                                                                                                                                                                                     
 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z50x.bin                                                                                                                                                                                     
 L

ld: warning: ignoring duplicate libraries: '-lblas', '-llapack', '-lz'


run inlist_evolve_header
DATE: 2025-08-07
TIME: 02:45:02
 reading user weak rate file /Users/emily/mesa-24.08.1/data/rates_data/rate_tables/S13_r_be7_wk_li7.h5
 version_number r24.08.1
 read inlist_evolve
 extras_controls: eos initialized
load saved model /Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models/uniform_relaxed/planet_relax_0.41_Mj_2.0_Rj_zbar=0.1_uniform_s=11.0.mod

 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z00x.bin                                                                                                                                                                                     
 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z50x.bin                                                                                                                                                                                     
 L

ld: warning: ignoring duplicate libraries: '-lblas', '-llapack', '-lz'


run inlist_evolve_header
DATE: 2025-08-07
TIME: 02:53:40
 reading user weak rate file /Users/emily/mesa-24.08.1/data/rates_data/rate_tables/S13_r_be7_wk_li7.h5
 version_number r24.08.1
 read inlist_evolve
 extras_controls: eos initialized
load saved model /Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models/uniform_relaxed/planet_relax_0.41_Mj_2.0_Rj_zbar=0.1_uniform_s=11.0.mod

 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z00x.bin                                                                                                                                                                                     
 Load1_eosDT_Table ep% tbl1     4392286
 /Users/emily/mesa-24.08.1/data/eosDT_data/cache/mesa-planetblend_00z50x.bin                                                                                                                                                                                     
 L

# Inert core model (needs to be run separately bc it's based on the "make_planet" test suite example, which has an inert z=1 core)

In [ ]:
comps = ['inert_core']

In [ ]:
os.chdir('/Users/emily/Documents/astro/giant_planets/science_runs/3_evolved_models/evolve_inert_core_models')

create_models_dir = '/Users/emily/Documents/astro/giant_planets/science_runs/1_created_models'
relax_models_dir = '/Users/emily/Documents/astro/giant_planets/science_runs/2_relaxed_models'
evolve_models_dir = '/Users/emily/Documents/astro/giant_planets/science_runs/3_evolved_models'

for i, m in enumerate(Minit):
    for j, r in enumerate(Rinit):
        for k, z in enumerate(Zinit):
            for l, comp in enumerate(comps):
                for n, s in enumerate(Sinit):
                    for a, alpha in enumerate(alphas):

                        this_comp_dir_relax = "{0}_relaxed".format(comp)
                        this_comp_dir_evolve = "{0}_evolved".format(comp)
                        
                        inlist_evolve = mh.Inlist('./inlist_evolve')
                        relax_model_filename = "{0}/{1}/planet_relax_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}.mod".format(relax_models_dir, this_comp_dir_relax, m, r, z, comp, s)
                        
                        evolve_model_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}.mod".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        evolve_profile_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}.profile".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        history_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}.history".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        profile_folder_filename = "{0}/{1}/planet_evolve_{2}_Mj_{3}_Rj_zbar={4}_{5}_s={6}_alpha={7}_profiles/".format(evolve_models_dir, this_comp_dir_evolve, m, r, z, comp, s, alpha)
                        
                        # only proceed if (1) the 'relaxed' model for the above parameter combination exists and 
                        #                 (2) the 'evolved' model does not *yet* exist
                        if os.path.isfile(relax_model_filename) and not os.path.isfile(evolve_model_filename):
                            print("Minit is {0}, Rinit is {1}, Zinit is {2}, comp is {3}, Sinit is {4}".format(m,r,z,comp,s))
                            
                            inlist_evolve.set_option('load_model_filename', relax_model_filename)
                            inlist_evolve.set_option('save_model_filename', evolve_model_filename)
                            inlist_evolve.set_option('filename_for_profile_when_terminate', evolve_profile_filename)
                            inlist_evolve.set_option('mixing_length_alpha', alpha)
        
                            # edit rn script
                            f = open('./rn_template'.format(m), 'r')
                            g = f.read()
                            f.close()
                            #print(g)
                            #g = g.replace("<<relax_profile_name>>", relax_profile_filename)
                            g = g.replace("<<evolve_model_filename>>", evolve_model_filename)
                            
                            h = open('./rn_temp'.format(m), 'w')
                            h.write(g)
                            h.close()
                            shutil.copyfile('./rn_temp'.format(m),'./rn'.format(m))
                            
                            # execute mk, rn scripts
                            os.system('./mk')
                            os.system('./rn')
                            os.system('mv ./LOGS/history.data {0}'.format(history_filename))
                            os.system('mkdir {0}'.format(profile_folder_filename))
                            os.system('mv ./LOGS/profile*.data {0}'.format(profile_folder_filename))
                            os.system('rm ./LOGS/*')
                            
                            print("")
                            print("")
                            
                        else:
                            continue
                            